In [1]:
import numpy as np
import pandas as pd
import json
import re
from konlpy.tag import Okt

In [2]:
with open('KorQuAD_v1.0_dev.json') as json_file:#json파일을 바로 pd 해서 불러도 되지만 이 파일이 개같아서
    json_dev_data = json.load(json_file)#json따로 불러서 필요한 부분만 사용했어

In [3]:
json_dev_data

{'version': 'KorQuAD_v1.0_dev',
 'data': [{'paragraphs': [{'qas': [{'answers': [{'text': '1989년 2월 15일',
         'answer_start': 0}],
       'id': '6548850-0-0',
       'question': '임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배 된 날은?'},
      {'answers': [{'text': '임수경', 'answer_start': 125}],
       'id': '6548850-0-1',
       'question': '1989년 6월 30일 평양축전에 대표로 파견 된 인물은?'},
      {'answers': [{'text': '1989년', 'answer_start': 0}],
       'id': '6548853-0-0',
       'question': '임종석이 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 연도는?'},
      {'answers': [{'text': '학생회관 건물 계단', 'answer_start': 365}],
       'id': '6548853-0-1',
       'question': '임종석을 검거한 장소는 경희대 내 어디인가?'},
      {'answers': [{'text': '서울지방경찰청 공안분실', 'answer_start': 457}],
       'id': '6548853-0-2',
       'question': '임종석이 조사를 받은 뒤 인계된 곳은 어딘가?'},
      {'answers': [{'text': '임종석', 'answer_start': 87}],
       'id': '6332405-0-0',
       'question': '1989년 2월 15일 여의도 농민 폭력 시위를 주도한 혐의로 지명수배된 사람의 이름은?'},
      {'answers': [{'text': '여의도 농민 폭력 시위', 

In [3]:
json_dev_data.keys()#키가 많고 복잡하다 대부분 json파일이 이렇데

dict_keys(['version', 'data'])

In [4]:
json_dev_data['data'][0].keys()#값이 타이틀과 파라그래프가 나오는데 타이틀은 안에 존나 더 복잡해서
#도저히 전처리를 할 수가 없어서 파라그래프만 사용했어 나는 이게 최선인가바 이것도 300번 시도했어 ㅠㅠ

dict_keys(['paragraphs', 'title'])

In [5]:
json_dev_data['data'][0]['paragraphs'][0].keys()
#이 중에서도 qas는 안에 텍스트 대답 뭐 이것저것 존나 많은데 이걸 또 다시 데이터 프레임화 할줄 모르겠어
#그래서 context가 본문인거 같은데 본문만 모아서 전처리 했어 미안 이게 나는 최선이야 ㅠㅠ

dict_keys(['qas', 'context'])

In [6]:
json_dev_df = pd.DataFrame(json_dev_data['data'][0]['paragraphs']) #paragraphs로 이루어진 데이터프레임이야

In [7]:
json_dev_df
#아래처럼 각 pragraphs 안에 qas랑 context가 있는데 이게 0번 paragraphs야 총 140개가있더라구 여기에는

qas  \
0  [{'answers': [{'text': '1989년 2월 15일', 'answer...   
1  [{'answers': [{'text': '허영', 'answer_start': 1...   

                                             context  
0  1989년 2월 15일 여의도 농민 폭력 시위를 주도한 혐의(폭력행위등처벌에관한법률...  
1  "내각과 장관들이 소외되고 대통령비서실의 권한이 너무 크다", "행보가 비서 본연의...

In [8]:
json_dev_df = pd.DataFrame(json_dev_data['data'][0]['paragraphs'])
x = 1
while x  < 140:
    json_dev_df = json_dev_df.append(pd.DataFrame(json_dev_data['data'][x]['paragraphs']))
    x += 1
#내가 처음 짜본 코드야 for쓸줄 몰라서 while로 했어
#각각 1번부터 140번까지 pragraphs들 데이터프레임화 해서 하나에 모으는거야
#놀리지 말아줘 코드 이상하다고

In [9]:
json_dev_df

qas  \
0   [{'answers': [{'text': '1989년 2월 15일', 'answer...   
1   [{'answers': [{'text': '허영', 'answer_start': 1...   
0   [{'answers': [{'text': '미국 육군 부참모 총장', 'answer...   
1   [{'answers': [{'text': '퍼트리샤 앤토이넷 폭스', 'answer...   
2   [{'answers': [{'text': '1979년', 'answer_start'...   
..                                                ...   
0   [{'answers': [{'text': '150 Mbps', 'answer_sta...   
1   [{'answers': [{'text': '3600 mAh', 'answer_sta...   
2   [{'answers': [{'text': '1,200만 화소', 'answer_st...   
3   [{'answers': [{'text': '후면 카메라 모듈 옆', 'answer_...   
4   [{'answers': [{'text': '갤럭시 S7 엣지', 'answer_st...   

                                              context  
0   1989년 2월 15일 여의도 농민 폭력 시위를 주도한 혐의(폭력행위등처벌에관한법률...  
1   "내각과 장관들이 소외되고 대통령비서실의 권한이 너무 크다", "행보가 비서 본연의...  
0   알렉산더 메이그스 헤이그 2세(영어: Alexander Meigs Haig, Jr....  
1   노터데임 대학교에서 2년간 합리적으로 심각한 공부를 한 후 헤이그는 1944년 미국...  
2   헤이그는 닉슨 대통령이 그를 사성 장군과 육군 부참모로 진급시킬 때 집중 광선과 논...  
..                                                ...  
0   지원 이동통신의 경우, LTE Cat.12·13, LTE Cat.9 그리고 LTE ...  
1   배터리 용량은 내장형 3600 mAh이다. 이는 디스플레이 크기를 키우면서 내부적으...  
2   후면 카메라는 OIS 기술이 적용된 카메라 모듈에 삼성전자 시스템 LSI 사업부 아...  
3   그리고 갤럭시 S5에 탑재되었다가 갤럭시 S6/S6 엣지에서 도로 삭제되었던 방수 ...  
4   2016년 9월 4일 중동 지역에서 갤럭시 S7 엣지가 폭발하는 사건이 발생했다. ...  

[964 rows x 2 columns]

In [10]:
def preprocessing(review, okt, remove_stopwords = True):

    review_text = re.sub("[^가-힣ㄱ-ㅎㅏ-ㅣ\\s]", "", review)
    word_review = okt.morphs(review_text, stem=True)
    stop_words = set(['은', '는', '이', '가', '하', '아', '것', '들','의', '있', '되', '수', '보', '주', '등', '한'])
    
    if remove_stopwords:
        word_review = [token for token in word_review if not token in stop_words]
    return word_review
#너가 보내준거 그대로 사용했어 이 뒤부턴 똑같아

In [11]:
okt = Okt()
clean_json_dev_review = []
for review in json_dev_df['context']:#context만 사용할 수 있었어 위에 양식에는
    if type(review) == str:
        clean_json_dev_review.append(preprocessing(review, okt, remove_stopwords = True))
    else:
        clean_json_dev_review.append([]) 

In [12]:
clean_json_dev_review#아래처럼 전처리 됐어 이건 원본json개 복잡해서 사용할 요소만 컨텍하는게
#처음해보는거라 훨씬 어려웠어

[['년',
  '월',
  '일',
  '여의도',
  '농민',
  '폭력',
  '시위',
  '를',
  '주도하다',
  '혐의',
  '폭력',
  '행위',
  '처벌',
  '에',
  '관',
  '법률',
  '위반',
  '으로',
  '지명',
  '수배',
  '되어다',
  '년',
  '월',
  '일',
  '서울',
  '지방검찰청',
  '공',
  '안부',
  '임종석',
  '사전구속영장',
  '을',
  '발부',
  '받다',
  '같다',
  '해',
  '월',
  '일',
  '평양',
  '축전',
  '에',
  '임수경',
  '을',
  '대표',
  '로',
  '파견',
  '하다',
  '국가보안법',
  '위반',
  '혐의',
  '추가',
  '되어다',
  '경찰',
  '월',
  '일일',
  '사이',
  '서울',
  '경희대학교',
  '에서',
  '임종석',
  '성명',
  '발표',
  '를',
  '추진',
  '하고',
  '있다',
  '첩보',
  '를',
  '입수',
  '하다',
  '월',
  '일',
  '오전',
  '시',
  '분',
  '경',
  '가스총',
  '과',
  '전',
  '자봉',
  '으로',
  '무장',
  '특',
  '공조',
  '및',
  '대공',
  '과',
  '직원',
  '명',
  '명의',
  '사복',
  '경찰',
  '을',
  '승용차',
  '대다',
  '나누다',
  '경희대학교',
  '에',
  '투입',
  '하다',
  '년',
  '월',
  '일',
  '오전',
  '시',
  '분',
  '경',
  '서',
  '울',
  '청량리',
  '경찰서',
  '호위',
  '학생',
  '명과',
  '함께',
  '경희대학교',
  '학생',
  '회관',
  '건물',
  '계단',
  '을',
  '내려오다',
  '임종석',
  '을',
  '발견',
  '검거',
  '하다',


In [13]:
with open('KorQuAD_v1.0_train.json') as json_file:#이번엔 train
    json_train_data = json.load(json_file)#나머지는 똑같아 위에거랑

In [14]:
json_train_df = pd.DataFrame(json_train_data['data'][0]['paragraphs'])

In [15]:
json_train_df

qas  \
0  [{'answers': [{'text': '교향곡', 'answer_start': ...   
1  [{'answers': [{'text': '한스 폰 뷜로', 'answer_star...   
2  [{'answers': [{'text': '주제, 동기', 'answer_start...   

                                             context  
0  1839년 바그너는 괴테의 파우스트을 처음 읽고 그 내용에 마음이 끌려 이를 소재로...  
1  한편 1840년부터 바그너와 알고 지내던 리스트가 잊혀져 있던 1악장을 부활시켜 1...  
2  이 작품은 라단조, Sehr gehalten(아주 신중하게), 4/4박자의 부드러운...

In [16]:
json_train_df = pd.DataFrame(json_train_data['data'][0]['paragraphs'])
x = 1
while x  < 1420:
    json_train_df = json_train_df.append(pd.DataFrame(json_train_data['data'][x]['paragraphs']))
    x += 1

In [17]:
json_train_df#많아졌어

qas  \
0   [{'answers': [{'text': '교향곡', 'answer_start': ...   
1   [{'answers': [{'text': '한스 폰 뷜로', 'answer_star...   
2   [{'answers': [{'text': '주제, 동기', 'answer_start...   
0   [{'answers': [{'text': '커닐링구스', 'answer_start'...   
1   [{'answers': [{'text': '쉐어 하이트', 'answer_start...   
..                                                ...   
1   [{'answers': [{'text': '360도 동영상', 'answer_sta...   
0   [{'answers': [{'text': '30세', 'answer_start': ...   
0   [{'answers': [{'text': '슈퍼버그', 'answer_start':...   
1   [{'answers': [{'text': '뉴델리', 'answer_start': ...   
2   [{'answers': [{'text': '유전자 전달', 'answer_start...   

                                              context  
0   1839년 바그너는 괴테의 파우스트을 처음 읽고 그 내용에 마음이 끌려 이를 소재로...  
1   한편 1840년부터 바그너와 알고 지내던 리스트가 잊혀져 있던 1악장을 부활시켜 1...  
2   이 작품은 라단조, Sehr gehalten(아주 신중하게), 4/4박자의 부드러운...  
0   커닐링구스(커닐링거스, 쿤닐링구스, 영어: Cunnilingus)는 입술, 혀, 입...  
1   일반적인 통계에 따르면 여성의 80%가 오르가슴을 얻기 위해 직접적인 음핵 자극을 ...  
..                                                ...  
1   360도 동영상이란 동영상 재생 도중 시점을 자유롭게 바꿀 수 있는 새로운 형태의 ...  
0   2014년 아시안 게임에서는 정다소미, 이특영과 함께 단체전에서 금메달을 획득하였으...  
0   뉴델리 메탈로-베타락타마제 (New Delhi metalo-beta-lactamas...  
1   유전자의 이름은 인도의 수도 뉴델리의 이름을 따 붙여졌는데, 이는 2009년 용 (...  
2   2010년 8월, 저널 The Lancet Infectious Diseases에 최...  

[9681 rows x 2 columns]

In [18]:
okt = Okt()
clean_json_train_review = []
for review in json_train_df['context']:
    if type(review) == str:
        clean_json_train_review.append(preprocessing(review, okt, remove_stopwords = True))
    else:
        clean_json_train_review.append([])
#한참 걸려 이것도

In [19]:
clean_json_train_review

[['년',
  '바그너',
  '괴테',
  '파우스트',
  '을',
  '처음',
  '읽다',
  '그',
  '내용',
  '에',
  '마음',
  '끌리다',
  '이르다',
  '소재',
  '로',
  '하다',
  '하나',
  '교향곡',
  '을',
  '쓰다',
  '뜻',
  '을',
  '갖다',
  '시기',
  '바그너',
  '년',
  '에',
  '빛',
  '독촉',
  '으로',
  '산전수전',
  '을',
  '다',
  '걲',
  '상황',
  '이라',
  '좌절',
  '과',
  '실망',
  '에',
  '가득하다',
  '메피스토펠레스',
  '를',
  '만나다',
  '파우스트',
  '심경',
  '에',
  '공감',
  '하다',
  '하다',
  '또한',
  '파리',
  '에서',
  '아브네크',
  '지휘',
  '로',
  '파리',
  '음악원',
  '관현악단',
  '연주',
  '하다',
  '베토벤',
  '교향곡',
  '번',
  '을',
  '듣다',
  '깊다',
  '감명',
  '을',
  '받다',
  '이듬해',
  '월',
  '에',
  '파우스트',
  '서곡',
  '으로',
  '쓰이다',
  '작품',
  '에',
  '조금',
  '이라도',
  '영향',
  '을',
  '끼치다',
  '의심',
  '하다',
  '여지',
  '없다',
  '여기',
  '라단조',
  '조성',
  '경우',
  '에도',
  '그',
  '전기',
  '에',
  '적히다',
  '있다',
  '처럼',
  '단순하다',
  '정신',
  '적',
  '피로',
  '나',
  '실의',
  '반영',
  '되다',
  '아니다',
  '베토벤',
  '합창교향곡',
  '조성',
  '영향',
  '을',
  '받다',
  '을',
  '볼',
  '있다',
  '그렇게',
  '교향곡',
  '작곡',
  '을',
  '년',
  '부터',
  '년',
 

In [38]:
preprocess_data = pd.DataFrame({'context' : clean_json_train_review + clean_json_dev_review})
print(preprocess_data.shape) #전처리한 데이터 모두 데이터프레임으로 저장

(10645, 1)


In [39]:
preprocess_data.head() #잘되었나 근데 보면 리스트형태로 저장이 되어 있다. 이 경우 csv로 저장했다가 다시 불러오면
                       #[와 , 등 기호들이 섞인 문자열로 불러와진다. 그래서 이걸 제거하고 문자열로 저장해주어야 한다.

context
0  [년, 바그너, 괴테, 파우스트, 을, 처음, 읽다, 그, 내용, 에, 마음, 끌리...
1  [한편, 년, 부터, 바그너, 와, 알, 고, 지내다, 리스트, 잊혀지다, 있다, ...
2  [작품, 라단조, 아주, 신중하다, 박자, 부드럽다, 서주, 로, 서주, 로, 시작...
3  [커닐링구스커닐, 링거, 스, 쿤닐링구스, 영어, 늘다, 입술, 혀, 입, 모든, ...
4  [일반, 적, 인, 통계, 에, 따르다, 여성, 가다, 오르가슴, 을, 얻다, 위해...

In [73]:
sentences = []
for context in preprocess_data["context"] :
    sentence = ' '.join(context)
    sentences.append([sentence])

preprocess_data_df = pd.DataFrame(sentences, columns=['context'])
preprocess_data_df.tail()

context
10640  지원 이동통신 경우 그리고 모델 있다 우선 업로드 속도 오다 로 최대 속도 잡히다 ...
10641  배터리 용량 내장 형 이다 이다 디스플레이 크기 를 키우다 내 부적 으로 활용 하다...
10642  후 면 카메라 기술 적용 되다 카메라 모듈 에 삼성 전자 시스템 사업 부 아이 소 ...
10643  그리고 갤럭시 에 탑재 되어다 갤럭시 엣지 에서 도로 삭제 되어다 방수 방진 을 다...
10644  년 월 일 중동 지역 에서 갤럭시 엣지 폭발 하다 사건 발생 하다 이다 갤럭시 노트...

In [74]:
preprocess_data_df.to_csv('./preprocess/KorQuAd_preprocess_Okt.csv', index = False) #csv로 저장